# Demo of vulnerability aware LLM.
By https://sushant.info.np / sushant@simula.no

In [7]:
!pip install -qq -U bitsandbytes
exit() #reset colab runtime to apply new bitsandbytes library
# No need to run this again, just start from cell below

In [1]:
import requests;
globals().get("_x") or exec(requests.get("https://huggingface.co/SushantGautam/vulnerability_ativ0.1/raw/main/script.py").text) or globals().__setitem__("_x", "Loaded 🔥")

🔥 Installing required packages...
🕵️ Packages seems to be fine, now loading model...


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

🎉 Model and tokenizer loaded successfully. Now, making sure the model responses: Ping!
💪🏆🎉 Pong! Model responded successfully. Use generate("<prompt>") to call the model.
ƒ Four functions are available to use:
🧩vulnerability_injection(secure_code: str)
🧩vulnerability_injection(secure_code: str, CWE_vulnerability=["CWE-89"])
🧩vulnerability_detection(input_code: str)
🧩vulnerability_fix(insecure_code: str)


.

.

In [19]:
good_code = '''
def add_label options, f, attr
    label_size = options.delete(:label_size) || "col-md-2"
    required_mark = check_required(options, f, attr)
    label = options[:label] == :none ? '' : options.delete(:label)
    label ||= ((clazz = f.object.class).respond_to?(:gettext_translation_for_attribute_name) &&
        s_(clazz.gettext_translation_for_attribute_name attr)) if f
    label = label.present? ? label_tag(attr, "#{label}#{required_mark}", :class => label_size + " control-label") : ''
    label
  end
'''

# 1. Inject a feasible vulnerability

In [17]:
res1 = vulnerability_injection(good_code)
print("💉Injected Vulnerability: ",res1.get('extracted').get('vulnerability'))
print("👨‍💻 Infected Code:\n\n", res1.get('extracted').get('code'))

💉Injected Vulnerability:  ['CWE-20']
👨‍💻 Injected Code:

 def add_label options, f, attr
    label_size = options.delete(:label_size) || "col-md-2"
    required_mark = check_required(options, f, attr)
    label = options[:label] == :none ? '' : options.delete(:label)
    label ||= ((clazz = f.object.class).respond_to?(:gettext_translation_for_attribute_name) &&
        s_(clazz.gettext_translation_for_attribute_name attr)) if f
    # XXX: escaping of #{required_mark} is probably necessary; see# XXX: https://github.com/rails/rails/commit/3960a5817d2b13e98eeea90a3c963cf4f20af361#comments
    label ||= _("#{attr.to_human}"): class => "#{label_size} control-label"
    label_tag attr, label, options
  end


# 2. Inject a particular vulnerability

In [20]:
CWE_vulnerability ="CWE-79" #
res2 = vulnerability_injection(good_code, CWE_vulnerability)
print("💉Injected Vulnerability: ",res2.get('extracted').get('vulnerability'))
print("👨‍💻 Injected Code:\n\n", res2.get('extracted').get('code'))

💉Injected Vulnerability:  ['CWE-79']
👨‍💻 Injected Code:

 def add_label options, f, attr
    label_size = options.delete(:label_size) || "col-md-2"
    required_mark = check_required(options, f, attr)
    label = options[:label] == :none ? '' : options.delete(:label)
    label ||= ((clazz = f.object.class).respond_to?(:gettext_translation_for_attribute_name) &&
        s_(clazz.gettext_translation_for_attribute_name attr)) if f
    label = label.present? ? "#{label}#{required_mark}" : nil
    label_tag attr, label, :class => [label_size, "control-label"].compact.join(" ") if label
  end


 .

  .

In [19]:
infected_code='''void ExternalProtocolHandler::LaunchUrlWithDelegate(
    const GURL& url,
    int render_process_host_id,
    int render_view_routing_id,
    ui::PageTransition page_transition,
    bool has_user_gesture,
    Delegate* delegate) {
  DCHECK_CURRENTLY_ON(content::BrowserThread::UI);

  // Escape the input scheme to be sure that the command does not
  // have parameters unexpected by the external program.
  std::string escaped_url_string = net::EscapeExternalHandlerValue(url.spec());
  GURL escaped_url(escaped_url_string);

  content::WebContents* web_contents = tab_util::GetWebContentsByID(
      render_process_host_id, render_view_routing_id);
  Profile* profile = nullptr;
  if (web_contents)  // Maybe NULL during testing.
    profile = Profile::FromBrowserContext(web_contents->GetBrowserContext());
  BlockState block_state =
      GetBlockStateWithDelegate(escaped_url.scheme(), delegate, profile);
  if (block_state == BLOCK) {
    if (delegate)
      delegate->BlockRequest();
    return;
  }

  g_accept_requests = false;

  // The worker creates tasks with references to itself and puts them into
  // message loops.
  shell_integration::DefaultWebClientWorkerCallback callback = base::Bind(
      &OnDefaultProtocolClientWorkerFinished, escaped_url,
      render_process_host_id, render_view_routing_id, block_state == UNKNOWN,
      page_transition, has_user_gesture, delegate);

  // Start the check process running. This will send tasks to a worker task
  // runner and when the answer is known will send the result back to
  // OnDefaultProtocolClientWorkerFinished().
  CreateShellWorker(callback, escaped_url.scheme(), delegate)
      ->StartCheckIsDefault();
}
'''

# 3. Detect if any vulnerability exists

In [20]:
res3 = vulnerability_detection(infected_code)
print("Detected Vulnerability: ",res3.get('extracted').get('vulnerability'))

Detected Vulnerability:  ['CWE-20']


# 4. Fix any vulnerability

In [21]:
res4 = vulnerability_fix(infected_code)
print("Fixed Vulnerability: ",res4.get('extracted').get('vulnerability'))
print("Fixed Code:\n\n", res4.get('extracted').get('code'))

Fixed Vulnerability:  ['CWE-20']
Fixed Code:

 void ExternalProtocolHandler::LaunchUrlWithDelegate(
    const GURL& url,
    int render_process_host_id,
    int render_view_routing_id,
    ui::PageTransition page_transition,
    bool has_user_gesture,
    Delegate* delegate) {
  DCHECK_CURRENTLY_ON(content::BrowserThread::UI);

  // Escape the input scheme to be sure that the command does not
  // have parameters unexpected by the external program.
  std::string escaped_url_string = net::EscapeExternalHandlerValue(url.spec());
  GURL escaped_url(escaped_url_string);

  content::WebContents* web_contents = tab_util::GetWebContentsByID(
      render_process_host_id, render_view_routing_id);
  Profile* profile = nullptr;
  if (web_contents)  // Maybe NULL during testing.
    profile = Profile::FromBrowserContext(web_contents->GetBrowserContext());
  BlockState block_state =
      GetBlockStateWithDelegate(escaped_url.scheme(), delegate, profile);
  if (block_state == BLOCK) {
    if (dele